In [281]:
import os
import numpy as np
import pandas as pd
import librosa as lr
import librosa.display
import glob
import matplotlib.pyplot as plt
import moviepy.editor as mp
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import OneHotEncoder
from sklearn.metrics import confusion_matrix, classification_report
from sklearn.ensemble import RandomForestClassifier
from keras.models import Sequential
from keras.layers import Dense, Dropout, Flatten, Conv1D, MaxPooling1D, LSTM
from keras.utils import to_categorical
from keras.callbacks import EarlyStopping, ModelCheckpoint

In [137]:
EMOTIONS = {1:'neutral', 2:'calm', 3:'happy', 4:'sad', 5:'angry', 6:'fear', 7:'disgust', 0:'surprise'}

In [138]:
data = pd.DataFrame(columns=['Emotion', 'Emotion intensity', 'Gender','Path'])

In [139]:
dataset = []
files = glob.glob(fr'C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\projet_dl\projet_DL\dataset\*')
for folders in files:
    folder1 = glob.glob(fr'{folders}\*')
    
    dataset.extend(folder1)
    
    print(dataset)

['C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-01-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-01-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-02-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-02-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-01-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-01-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-02-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-02-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\EC

In [140]:
print(len(dataset))

2452


In [336]:
# Définir une fonction pour extraire les caractéristiques audio
def extract_features(file_path):
    # Charger le fichier audio avec Librosa
    y, sr = lr.load(file_path, sr=None)
    
    # Calculer le spectre mél
    mel_spec = librosa.feature.melspectrogram(y=y, sr=sr)
    
    # Calculer les coefficients cepstraux en fréquence (MFCC)
    mfcc = librosa.feature.mfcc(y=y, sr=sr, n_mfcc=13)  
    
    # Calculer le chromagramme
    chroma = librosa.feature.chroma_stft(y=y, sr=sr)
    
    # Calculer le rythme
    tempo, _ = librosa.beat.beat_track(y=y, sr=sr)

    return mel_spec, mfcc, chroma, tempo

In [364]:
# Définir les émotions
EMOTIONS = {1: 'neutral', 2: 'calm', 3: 'happy', 4: 'sad', 5: 'angry', 6: 'fear', 7: 'disgust', 8: 'surprise'}

# Chemin du dossier contenant les fichiers audio
DATA_PATH = fr'C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\projet_dl\projet_DL\dataset'

# Définir la liste pour stocker les données
data = []

# Parcourir les dossiers
folders = glob.glob(os.path.join(DATA_PATH, '*'))
for folder in folders:
    # Parcourir les fichiers dans chaque dossier
    folder1 = glob.glob(os.path.join(folder, '*'))
    for files1 in folder1:
        data1 = glob.glob(os.path.join(files1, '*'))
        
        y, sr = lr.load(files1, sr=None)
            
        # Extraire les informations du fichier
        identifiers = os.path.basename(files1).split('.')[0].split('-')
            
        modality = int(identifiers[0])
        vocal_channel = int(identifiers[1])
        emotion = int(identifiers[2])
        emotion_intensity = int(identifiers[3])
        statement = int(identifiers[4])
        repetition = int(identifiers[5])
        actor = int(identifiers[6])
            
        # Mapping des informations pour correspondre à notre structure
        emotion_mapping = {1: 'neutral', 2: 'calm', 3: 'happy', 4: 'sad', 5: 'angry', 6: 'fear', 7: 'disgust', 8: 'surprise'}
        #emotion = emotion_mapping[emotion]
        emotion_intensity = 'normal' if emotion_intensity == 1 else 'strong'            
        gender = 'female' if actor % 2 == 0 else 'male'
            
        # Ajouter les informations au DataFrame
        data.append({
            'Modality': modality,
            'Vocal Channel': vocal_channel,
            'Emotion': emotion,
            'Emotion_string': emotion_mapping[emotion],
            'Emotion Intensity': emotion_intensity,
            'Statement': statement,
            'Repetition': repetition,
            'Actor': actor,
            'Gender': gender,
            'Path': files1
         })

# Convertir la liste en DataFrame
df = pd.DataFrame(data)

# Afficher le DataFrame
print(df)

      Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0            3              1        1        neutral            normal   
1            3              1        1        neutral            normal   
2            3              1        1        neutral            normal   
3            3              1        1        neutral            normal   
4            3              1        2           calm            normal   
...        ...            ...      ...            ...               ...   
2447         3              2        6           fear            normal   
2448         3              2        6           fear            strong   
2449         3              2        6           fear            strong   
2450         3              2        6           fear            strong   
2451         3              2        6           fear            strong   

      Statement  Repetition  Actor  Gender  \
0             1           1      1    male   
1      

In [365]:
for index, row in df.iterrows():
    file_path = row['Path']
    mel_spec, mfcc, chroma, tempo = extract_features(file_path)
    
    # Stockez les caractéristiques résumées dans le DataFrame
    df.at[index, 'Mel Spectrogram'] = mel_spec.mean()
    #df.at[index, 'MFCC'] = mfcc.mean()
    df.at[index, 'Chroma'] = chroma.mean()            
    df.at[index, 'Tempo'] = tempo

In [ ]:
mfcc.shape

(13, 417)

In [ ]:
print(np.unique(mfcc))

[-651.8455  -651.82416 -651.8156  ...  151.13235  168.0095   175.51407]


In [366]:
# Convertir les données en type float32
mfcc_data = np.array(mfcc, dtype=np.float32)

# Transposer les données
mfcc_data_transposed = np.transpose(mfcc_data)

# Créer le DataFrame
df1 = pd.DataFrame(data=mfcc_data_transposed)

In [368]:
df1[0].unique()

array([-651.8455 , -647.67316, -638.62036, -645.91174, -650.827  ,
       -650.72363, -651.8145 , -651.1502 , -645.12054, -641.9631 ,
       -639.6444 , -632.624  , -629.1628 , -628.4438 , -624.01196,
       -623.9605 , -622.5034 , -622.93774, -627.8169 , -624.9069 ,
       -619.9364 , -614.7377 , -614.62   , -614.0814 , -615.8278 ,
       -618.31177, -619.0157 , -622.91223, -629.77264, -625.7462 ,
       -627.66895, -634.79987, -641.00256, -639.8442 , -639.7575 ,
       -645.6258 , -648.3934 , -649.9012 , -651.4582 , -651.6684 ,
       -651.3482 , -630.3983 , -557.93805, -513.82404, -538.7532 ,
       -604.03687, -634.4126 , -649.7652 , -635.86475, -593.70905,
       -589.4935 , -614.48956, -638.3165 , -645.73615, -474.92108,
       -330.24747, -274.93826, -284.41876, -301.4748 , -290.30786,
       -288.3576 , -297.34848, -315.71066, -335.37418, -354.40244,
       -371.3629 , -375.295  , -378.38077, -374.9255 , -360.75186,
       -351.72064, -333.03772, -297.98224, -271.3339 , -255.47

In [369]:
df2=pd.concat([df, df1], axis=1)

In [372]:
df2.iloc[:, -13:] = df2.iloc[:, -13:].fillna(0)

In [374]:
df2.columns

Index([         'Modality',     'Vocal Channel',           'Emotion',
          'Emotion_string', 'Emotion Intensity',         'Statement',
              'Repetition',             'Actor',            'Gender',
                    'Path',   'Mel Spectrogram',            'Chroma',
                   'Tempo',                   0,                   1,
                         2,                   3,                   4,
                         5,                   6,                   7,
                         8,                   9,                  10,
                        11,                  12],
      dtype='object')

In [376]:
last_n_columns = df2.iloc[:, -16:]
print(last_n_columns)

      Mel Spectrogram    Chroma       Tempo          0    1    2    3    4  \
0            0.002952  0.633091  187.500000 -651.84552  0.0  0.0  0.0  0.0   
1            0.003416  0.629568  106.132075 -651.84552  0.0  0.0  0.0  0.0   
2            0.004721  0.619984   82.720588 -651.84552  0.0  0.0  0.0  0.0   
3            0.004341  0.612607   66.176471 -651.84552  0.0  0.0  0.0  0.0   
4            0.001624  0.608243  112.500000 -651.84552  0.0  0.0  0.0  0.0   
...               ...       ...         ...        ...  ...  ...  ...  ...   
2447         0.037530  0.380013  160.714286    0.00000  0.0  0.0  0.0  0.0   
2448         0.118704  0.384475   86.538462    0.00000  0.0  0.0  0.0  0.0   
2449         0.126680  0.379459  193.965517    0.00000  0.0  0.0  0.0  0.0   
2450         0.122824  0.393004  114.795918    0.00000  0.0  0.0  0.0  0.0   
2451         0.208337  0.397366  181.451613    0.00000  0.0  0.0  0.0  0.0   

        5    6    7    8    9   10   11   12  
0     0.0  0.0  

In [379]:
# Normaliser les caractéristiques
scaler = StandardScaler()
df2[['Mel Spectrogram', 'Chroma', 'Tempo']] = scaler.fit_transform(df2[['Mel Spectrogram', 'Chroma', 'Tempo']])

In [380]:
print(df2.head())

   Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0         3              1        1        neutral            normal   
1         3              1        1        neutral            normal   
2         3              1        1        neutral            normal   
3         3              1        1        neutral            normal   
4         3              1        2           calm            normal   

   Statement  Repetition  Actor Gender  \
0          1           1      1   male   
1          1           2      1   male   
2          2           1      1   male   
3          2           2      1   male   
4          1           1      1   male   

                                                Path  ...    3    4    5    6  \
0  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...  0.0  0.0  0.0  0.0   
1  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...  0.0  0.0  0.0  0.0   
2  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...  0.0  0.0  0.

In [383]:
# Convertir les étiquettes d'émotion en encodage one-hot
le = LabelEncoder()
df2['Emotion'] = le.fit_transform(df2['Emotion'])
y = to_categorical(df2['Emotion'], len(EMOTIONS))

# Séparer les données en ensembles d'entraînement et de test
X_train, X_test, y_train, y_test = train_test_split(df2.iloc[:, -16:], y, test_size=0.2, random_state=42)

In [384]:
print(y)
print(y.shape)

[[1. 0. 0. ... 0. 0. 0.]
 [1. 0. 0. ... 0. 0. 0.]
 [1. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 1. 0. 0.]
 [0. 0. 0. ... 1. 0. 0.]
 [0. 0. 0. ... 1. 0. 0.]]
(2452, 8)


In [385]:
print(X_train.shape, X_test.shape, y_train.shape, y_test.shape)
print(y_train)
print("------")
print(y_test)

(1961, 16) (491, 16) (1961, 8) (491, 8)
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 1. 0.]
 [0. 0. 1. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 1. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
------
[[0. 0. 1. ... 0. 0. 0.]
 [0. 0. 1. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 1. 0. ... 0. 0. 0.]
 [0. 0. 1. ... 0. 0. 0.]]


In [386]:
# Définir le modèle
model = Sequential()
early_stopping = EarlyStopping(patience=15, restore_best_weights=True)
model_checkpoint = ModelCheckpoint('best_model_weights.h5', save_best_only=True)

#add cnn model
model.add(Conv1D(256, 5, padding='same', input_shape=(X_train.shape[1],1)))
model.add(MaxPooling1D(pool_size=2, padding='same'))
model.add(Dropout(0.5))

model.add(Conv1D(128, 5, padding='same'))
model.add(MaxPooling1D(pool_size=2, padding='same'))
model.add(Dropout(0.5))

# Ajouter une couche LSTM
model.add(LSTM(64, return_sequences=True))
model.add(LSTM(32, return_sequences=True))

model.add(Flatten())
model.add(Dense(256, activation='relu'))
model.add(Dense(len(EMOTIONS), activation='softmax'))

# Compiler le modèle
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# Entraîner le modèle
model.fit(X_train, y_train, epochs=80, batch_size=64, validation_split=0.2, verbose=1, callbacks=[early_stopping, model_checkpoint])

# Prédire sur l'ensemble de test
y_pred = model.predict(X_test)
y_pred_labels = np.argmax(y_pred, axis=1)
y_test_labels = np.argmax(y_test, axis=1)

Epoch 1/80
25/25 [==============================] - 11s 102ms/step - loss: 2.0618 - accuracy: 0.1601 - val_loss: 2.0346 - val_accuracy: 0.1883
Epoch 2/80
25/25 [==============================] - 1s 26ms/step - loss: 2.0340 - accuracy: 0.1798 - val_loss: 2.0171 - val_accuracy: 0.1603
Epoch 3/80
25/25 [==============================] - 1s 26ms/step - loss: 2.0165 - accuracy: 0.1907 - val_loss: 1.9750 - val_accuracy: 0.1883
Epoch 4/80
25/25 [==============================] - 1s 25ms/step - loss: 1.9694 - accuracy: 0.2009 - val_loss: 1.9454 - val_accuracy: 0.2188
Epoch 5/80
25/25 [==============================] - 1s 26ms/step - loss: 1.9213 - accuracy: 0.2366 - val_loss: 1.9336 - val_accuracy: 0.1883
Epoch 6/80
25/25 [==============================] - 1s 26ms/step - loss: 1.9126 - accuracy: 0.2455 - val_loss: 1.9111 - val_accuracy: 0.2087
Epoch 7/80
25/25 [==============================] - 1s 26ms/step - loss: 1.8941 - accuracy: 0.2513 - val_loss: 1.9038 - val_accuracy: 0.2214
Epoch 8/80


In [387]:
print(model.summary())

Model: "sequential_96"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d_248 (Conv1D)         (None, 16, 256)           1536      
                                                                 
 max_pooling1d_39 (MaxPooli  (None, 8, 256)            0         
 ng1D)                                                           
                                                                 
 dropout_87 (Dropout)        (None, 8, 256)            0         
                                                                 
 conv1d_249 (Conv1D)         (None, 8, 128)            163968    
                                                                 
 max_pooling1d_40 (MaxPooli  (None, 4, 128)            0         
 ng1D)                                                           
                                                                 
 dropout_88 (Dropout)        (None, 4, 128)          

In [280]:

# Définir le modèle
model = Sequential()

# Ajouter les couches entièrement connectées
model.add(Dense(128, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(64, activation='relu'))
model.add(Dense(len(EMOTIONS), activation='softmax'))

# Compiler le modèle
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# Entraîner le modèle
model.fit(X_train, y_train, epochs=15, batch_size=32, validation_split=0.2, verbose=1)

# Prédire sur l'ensemble de test
y_pred = model.predict(X_test)
y_pred_labels = np.argmax(y_pred, axis=1)
y_test_labels = np.argmax(y_test, axis=1)

# Évaluer les performances
accuracy = accuracy_score(y_test_labels, y_pred_labels)
conf_mat = confusion_matrix(y_test_labels, y_pred_labels)
class_report = classification_report(y_test_labels, y_pred_labels)

print(f'Accuracy: {accuracy}')
print(f'Confusion Matrix:\n{conf_mat}')
print(f'Classification Report:\n{class_report}')

Epoch 1/15
49/49 [==============================] - 2s 11ms/step - loss: 2.0215 - accuracy: 0.1913 - val_loss: 1.9456 - val_accuracy: 0.2087
Epoch 2/15
49/49 [==============================] - 0s 4ms/step - loss: 1.9357 - accuracy: 0.2449 - val_loss: 1.9132 - val_accuracy: 0.2061
Epoch 3/15
49/49 [==============================] - 0s 5ms/step - loss: 1.8953 - accuracy: 0.2583 - val_loss: 1.8946 - val_accuracy: 0.2239
Epoch 4/15
49/49 [==============================] - 0s 4ms/step - loss: 1.8625 - accuracy: 0.2730 - val_loss: 1.8835 - val_accuracy: 0.2417
Epoch 5/15
49/49 [==============================] - 0s 5ms/step - loss: 1.8475 - accuracy: 0.2755 - val_loss: 1.8579 - val_accuracy: 0.2570
Epoch 6/15
49/49 [==============================] - 0s 4ms/step - loss: 1.8293 - accuracy: 0.2844 - val_loss: 1.8573 - val_accuracy: 0.2468
Epoch 7/15
49/49 [==============================] - 0s 4ms/step - loss: 1.8265 - accuracy: 0.2902 - val_loss: 1.8563 - val_accuracy: 0.2824
Epoch 8/15
49/49 [=

In [15]:
mel_spectrograms = []
signals = []
for i, file_path in enumerate(df['Path']):
    audio, sample_rate = lr.load(file_path, duration=3, offset=0.5, sr=sr)
    signal = np.zeros((int(sr*3,)))
    signal[:len(audio)] = audio
    signals.append(signal)
    print("\r Processed {}/{} files".format(i, len(df)), end='')
signals = np.stack(signals, axis=0)

 Processed 1959/1960 files

La liste signals stocke les signaux audio extraits de chaque fichier. Chaque élément de la liste est un tableau NumPy représentant un signal audio de 3 secondes, ou de la durée spécifiée. Ces signaux seront utilisés comme données d'entrée pour la suite du prétraitement.

Une boucle itère sur chaque chemin de fichier dans la colonne 'Path' du DataFrame df.

Utilisation de la fonction load de Librosa pour charger le fichier audio à partir du chemin spécifié (file_path). Les paramètres duration=3 et offset=0.5 spécifient la durée du fichier audio à charger (3 secondes) et le décalage (offset) à partir du début du fichier (0.5 seconde). 

signal = np.zeros((int(SAMPLE_RATE * 3,))) : Création d'un tableau NumPy de taille correspondant à 3 secondes de signal audio (ou la durée spécifiée) avec un échantillonnage constant. On initialise ce tableau avec des zéros.

signal[:len(audio)] = audio : Remplissage de la partie du tableau avec le signal audio réel chargé. Cela permet d'ajuster la longueur du signal si elle est inférieure à 3 secondes.

signals = np.stack(signals, axis=0) : Conversion de la liste signals en un tableau NumPy bidimensionnel où chaque ligne représente un signal audio. Le résultat est stocké dans la variable signals qui sera utilisée ultérieurement dans le script.
